<h2> TRhis notebook is for testing models against common_voice (v7) </h2>




##### TEST WITH RASMUS 1B model with language model added using our own common_voice v7 (processed before event) ###

In [1]:
# Environment settings: 
import pandas as pd
pd.set_option('display.max_column', None)
pd.set_option('display.max_rows', None)
pd.set_option('display.max_seq_items', None)
pd.set_option('display.max_colwidth', 500)
pd.set_option('expand_frame_repr', True)

from datasets import concatenate_datasets, load_dataset

In [2]:
from huggingface_hub import notebook_login

notebook_login()

In [3]:
!git config --global credential.helper store

In [4]:
%%capture
!apt install git-lfs

In [5]:
# then git clone all datasets to local
!rm -r -f common_voice_fi
!git clone https://huggingface.co/datasets/Finnish-NLP/common_voice_fi common_voice_fi

Cloning into 'common_voice_fi'...
remote: Enumerating objects: 19431, done.
remote: Counting objects: 100% (19431/19431), done.
remote: Compressing objects: 100% (19392/19392), done.
remote: Total 19431 (delta 54), reused 19388 (delta 36)MiB/s   
Receiving objects: 100% (19431/19431), 258.56 MiB | 33.70 MiB/s, done.
Resolving deltas: 100% (54/54), done.
Checking out files: 100% (9700/9700), done.


In [6]:
import librosa
import torchaudio
from datasets import load_dataset, load_metric, Audio

In [7]:
import torch
from datasets import load_dataset, load_metric, Audio
from transformers import AutoModelForCTC, AutoProcessor, Wav2Vec2ProcessorWithLM
import librosa
import torchaudio
import torchaudio.functional as F

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

model_id = "RASMUS/wav2vec2-xlsr-fi-lm-1B"

model = AutoModelForCTC.from_pretrained(model_id).to(device)
processor = Wav2Vec2ProcessorWithLM.from_pretrained(model_id)


In [8]:
import os
current_path = os.getcwd()


common_voice_test = load_dataset('csv', data_files=[f'{current_path}/common_voice_fi/common_voice_fi.csv'], delimiter=',', column_names=['client_id','path','sentence','up_votes','down_votes','age','gender','accent','locale','segment','split','audio','dataset_name','filename'], split='train')
common_voice_test = common_voice_test.filter(lambda example: example['split'] in ['test'])


Using custom data configuration default-0b4c09e3fdd55089


  0%|          | 0/1 [00:00<?, ?it/s]

  0%|          | 0/1 [00:00<?, ?it/s]

Dataset csv downloaded and prepared to /workspace/.cache/huggingface/datasets/csv/default-0b4c09e3fdd55089/0.0.0/6b9057d9e23d9d8a2f05b985917a0da84d70c5dae3d22ddd8a3f22fb01c69d9e. Subsequent calls will reuse this data.


  0%|          | 0/15 [00:00<?, ?ba/s]

In [9]:
common_voice_test[0]

{'client_id': '635303a7d1e2ea13318960e7d71fd39251278ed8c30a11f4dc2db03ea528e70f67f5474f820bf938baaa12e5b6d6c76520e84ab3714bef5d86c86010f43de21e',
 'path': 'common_voice_fi_25838955.mp3',
 'sentence': 'Nyt en missään tapauksessa sinua auta.',
 'up_votes': '2',
 'down_votes': '0',
 'age': None,
 'gender': None,
 'accent': None,
 'locale': 'fi',
 'segment': None,
 'split': 'test',
 'audio': 'common_voice_fi_25838955.mp3',
 'dataset_name': 'common_voice_fi',
 'filename': 'common_voice_fi_25838955.mp3',
 '__index_level_0__': 0.0}

In [10]:
#### FIX PATHS
def fix_common_voice_path(batch):
    batch['path'] = os.getcwd()+ '/common_voice_fi/clips/' + batch['filename']
    batch['audio'] = batch['path']
    return batch

common_voice_test = common_voice_test.map(fix_common_voice_path)

  0%|          | 0/1599 [00:00<?, ?ex/s]

In [11]:
import re
CHARS_TO_IGNORE = [",", "?", "¿", ".", "!", "¡", ";", "；", ":", '""', "%", '"', "�", "ʿ", "·", "჻", "~", "՞",
                   "؟", "،", "।", "॥", "«", "»", "„", "“", "”", "「", "」", "‘", "’", "《", "》", "(", ")", "[", "]",
                   "{", "}", "=", "`", "_", "+", "<", ">", "…", "–", "°", "´", "ʾ", "‹", "›", "©", "®", "—", "→", "。",
                   "、", "﹂", "﹁", "‧", "～", "﹏", "，", "｛", "｝", "（", "）", "［", "］", "【", "】", "‥", "〽",
                   "『", "』", "〝", "〟", "⟨", "⟩", "〜", "：", "！", "？", "♪", "؛", "/", "\\", "º", "−", "^", "ʻ", "ˆ"]


chars_to_remove_regex = f"[{re.escape(''.join(CHARS_TO_IGNORE))}]"

def remove_special_characters(batch):
    batch["sentence"] = re.sub(chars_to_remove_regex, '', batch["sentence"]).lower()
    return batch

common_voice_test = common_voice_test.map(remove_special_characters)

  0%|          | 0/1599 [00:00<?, ?ex/s]

In [12]:
common_voice_test

Dataset({
    features: ['client_id', 'path', 'sentence', 'up_votes', 'down_votes', 'age', 'gender', 'accent', 'locale', 'segment', 'split', 'audio', 'dataset_name', 'filename', '__index_level_0__'],
    num_rows: 1599
})

In [13]:
common_voice_test_audio = common_voice_test.cast_column("audio", Audio(sampling_rate=16_000))


In [14]:
def prepare_dataset(batch):
    audio = batch["audio"]

    # batched output is "un-batched"
    batch["input_values"] = processor(audio["array"], sampling_rate=audio["sampling_rate"]).input_values[0]
    batch["input_length"] = len(batch["input_values"])
    batch["sentence"] = batch["sentence"]
    
    with processor.as_target_processor():
        batch["labels"] = processor(batch["sentence"]).input_ids
    return batch

In [15]:
common_voice_test_audio = common_voice_test_audio.map(prepare_dataset)

  0%|          | 0/1599 [00:00<?, ?ex/s]

In [16]:
#common_voice_test_audio[0]

{'client_id': '635303a7d1e2ea13318960e7d71fd39251278ed8c30a11f4dc2db03ea528e70f67f5474f820bf938baaa12e5b6d6c76520e84ab3714bef5d86c86010f43de21e',
 'path': '/workspace/xlsr_fi/common_voice_fi/clips/common_voice_fi_25838955.mp3',
 'sentence': 'nyt en missään tapauksessa sinua auta',
 'up_votes': '2',
 'down_votes': '0',
 'age': None,
 'gender': None,
 'accent': None,
 'locale': 'fi',
 'segment': None,
 'split': 'test',
 'audio': {'array': [0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   0.0,
   -3.561941713803307e-11,
   3.2315783382586005e

In [17]:
def evaluate(batch):
  inputs = processor(batch["input_values"], sampling_rate=16_000, return_tensors="pt", padding=True)

  with torch.no_grad():
    logits = model(inputs.input_values.to("cuda"), attention_mask=inputs.attention_mask.to("cuda")).logits

  pred_ids = torch.argmax(logits, dim=-1)
  batch["pred_strings"] = processor.batch_decode(pred_ids)
  return batch

def evaluate_with_lm(batch):
  inputs = processor(batch["input_values"], sampling_rate=16_000, return_tensors="pt", padding=True)

  with torch.no_grad():
    logits = model(inputs.input_values.to("cuda"), attention_mask=inputs.attention_mask.to("cuda")).logits
     
  batch["pred_strings"] = processor.batch_decode(logits.cpu().numpy()).text
  return batch



In [18]:
wer_metric = load_metric("wer")

In [19]:
#sample_1 = common_voice_test_audio.select([i for i in range(100)])
#result = sample_1.map(evaluate, batched=True, batch_size=8)
result_with_lm = common_voice_test_audio.map(evaluate_with_lm, batched=True, batch_size=8)


  0%|          | 0/200 [00:00<?, ?ba/s]

In [20]:
#### TAKE a look at pred / target

for i in range(10):
    print(str(i +1) + ". result")
    print("pred: " + str(result_with_lm[i]["pred_strings"]))
    print("sentence: " + str(result_with_lm[i]["sentence"]))
    print("#################")

1. result
pred: nyt en missään tapauksessa sinua auttaa
sentence: nyt en missään tapauksessa sinua auta
#################
2. result
pred: emme tarvitsisi äänestä toista vihonnista
sentence: emme tarvitsisi hänestä toista vihollista
#################
3. result
pred: matti vanha sen isä oli dosentti tatuvanhanen ja äiti rouva annitiihanen
sentence: matti vanhasen isä oli dosentti tatu vanhanen ja äiti rouva anni tiihonen
#################
4. result
pred: äänestin henkilökohtaisesti näiden tarkistusten puolesta
sentence: äänestin henkilökohtaisesti näiden tarkistusten puolesta
#################
5. result
pred: tunsin oloni loistavaksi kun olin saanut pojan paremmalle tuudelle
sentence: tunsin oloni loistavaksi kun olin saanut pojan paremmalle tuulelle
#################
6. result
pred: ankeriaskantojen elvyttämiseksi on päätetty vähentää ankeriaankalastusta puoleen
sentence: ankeriaskantojen elvyttämiseksi on päätetty vähentää ankeriaankalastusta puoleen
#################
7. result
pred: t

In [23]:
#result = test_dataset.map(evaluate, batched=True, batch_size=1)

print("WER: {:2f}".format(100 * wer_metric.compute(predictions=result_with_lm["pred_strings"], references=result_with_lm["sentence"])))

WER: 10.813813


<h3> Test from mozilla common_voice v_7_0 directly from hub 
Using currently the "old" preprocessing and not the "audio" method</h3

In [58]:
import torch
from datasets import load_dataset, load_metric, Audio
from transformers import AutoModelForCTC, AutoProcessor, Wav2Vec2ProcessorWithLM, AutoFeatureExtractor, pipeline
import librosa
import torchaudio
import torchaudio.functional as F

device = torch.device("cuda" if torch.cuda.is_available() else "cpu")

wer_metric = load_metric("wer")

model_id = "RASMUS/wav2vec2-xlsr-fi-lm-1B"

model = AutoModelForCTC.from_pretrained(model_id).to(device)
processor = Wav2Vec2ProcessorWithLM.from_pretrained(model_id)


In [25]:
common_voice_dataset = load_dataset("mozilla-foundation/common_voice_7_0", "fi", split="test")

Using the latest cached version of the module from /workspace/.cache/huggingface/modules/datasets_modules/datasets/mozilla-foundation--common_voice_7_0/33e08856cfa0d0665e837bcad73ffd920a0bc713ce8c5fffb55dbdf1c084d5ba (last modified on Sun Jan 23 16:17:44 2022) since it couldn't be found locally at mozilla-foundation/common_voice_7_0., or remotely on the Hugging Face Hub.
Reusing dataset common_voice (/workspace/.cache/huggingface/datasets/mozilla-foundation___common_voice/fi/7.0.0/33e08856cfa0d0665e837bcad73ffd920a0bc713ce8c5fffb55dbdf1c084d5ba)


In [26]:
import re
CHARS_TO_IGNORE = [",", "?", "¿", ".", "!", "¡", ";", "；", ":", '""', "%", '"', "�", "ʿ", "·", "჻", "~", "՞",
                   "؟", "،", "।", "॥", "«", "»", "„", "“", "”", "「", "」", "‘", "’", "《", "》", "(", ")", "[", "]",
                   "{", "}", "=", "`", "_", "+", "<", ">", "…", "–", "°", "´", "ʾ", "‹", "›", "©", "®", "—", "→", "。",
                   "、", "﹂", "﹁", "‧", "～", "﹏", "，", "｛", "｝", "（", "）", "［", "］", "【", "】", "‥", "〽",
                   "『", "』", "〝", "〟", "⟨", "⟩", "〜", "：", "！", "？", "♪", "؛", "/", "\\", "º", "−", "^", "ʻ", "ˆ"]


chars_to_remove_regex = f"[{re.escape(''.join(CHARS_TO_IGNORE))}]"

def remove_special_characters(batch):
    batch["sentence"] = re.sub(chars_to_remove_regex, '', batch["sentence"]).lower()
    return batch

common_voice_dataset = common_voice_dataset.map(remove_special_characters)

Loading cached processed dataset at /workspace/.cache/huggingface/datasets/mozilla-foundation___common_voice/fi/7.0.0/33e08856cfa0d0665e837bcad73ffd920a0bc713ce8c5fffb55dbdf1c084d5ba/cache-c01f9f0dd6942c15.arrow


In [27]:
def resample_audios(batch):
    sr = batch['audio']['sampling_rate']
    batch['audio']['array'] = F.resample(torch.tensor(batch["audio"]["array"]), sr, 16_000).numpy()
    return batch

common_voice_dataset = common_voice_dataset.map(resample_audios)

Loading cached processed dataset at /workspace/.cache/huggingface/datasets/mozilla-foundation___common_voice/fi/7.0.0/33e08856cfa0d0665e837bcad73ffd920a0bc713ce8c5fffb55dbdf1c084d5ba/cache-b66d07bf277a5504.arrow


In [28]:
def prepare_dataset(batch):
    batch["input_values"] = processor(batch["audio"]["array"], sampling_rate=16000).input_values[0]
    batch["input_length"] = len(batch["input_values"])
    batch["sentence"] = batch["sentence"]
    
    with processor.as_target_processor():
        batch["labels"] = processor(batch["sentence"]).input_ids
    return batch

In [29]:
common_voice_dataset = common_voice_dataset.map(prepare_dataset)

  0%|          | 0/1599 [00:00<?, ?ex/s]

In [30]:
wer_metric = load_metric("wer")

In [31]:
def evaluate_with_lm(batch):
  inputs = processor(batch["input_values"], sampling_rate=16_000, return_tensors="pt", padding=True)

  with torch.no_grad():
    logits = model(inputs.input_values.to("cuda"), attention_mask=inputs.attention_mask.to("cuda")).logits
     
  batch["pred_strings"] = processor.batch_decode(logits.cpu().numpy()).text
  return batch

In [32]:
result_with_lm = common_voice_dataset.map(evaluate_with_lm, batched=True, batch_size=8)
print("WER: {:2f}".format(100 * wer_metric.compute(predictions=result_with_lm["pred_strings"], references=result_with_lm["sentence"])))

  0%|          | 0/200 [00:00<?, ?ba/s]

WER: 13.489499



<h3> ASR PIPELINE PREDICTIONS (Same kind as in eval.py)</h3>



In [49]:
common_voice_dataset = load_dataset("mozilla-foundation/common_voice_7_0", "fi", split="test")

common_voice_dataset = common_voice_dataset.cast_column("audio", Audio(sampling_rate=16_000))

Using the latest cached version of the module from /workspace/.cache/huggingface/modules/datasets_modules/datasets/mozilla-foundation--common_voice_7_0/33e08856cfa0d0665e837bcad73ffd920a0bc713ce8c5fffb55dbdf1c084d5ba (last modified on Sun Jan 23 16:17:44 2022) since it couldn't be found locally at mozilla-foundation/common_voice_7_0., or remotely on the Hugging Face Hub.
Reusing dataset common_voice (/workspace/.cache/huggingface/datasets/mozilla-foundation___common_voice/fi/7.0.0/33e08856cfa0d0665e837bcad73ffd920a0bc713ce8c5fffb55dbdf1c084d5ba)


In [54]:
def normalize_text(text: str) -> str:
    """DO ADAPT FOR YOUR USE CASE. this function normalizes the target text."""

    chars_to_ignore_regex = [",", "?", "¿", ".", "!", "¡", ";", "；", ":", '""', "%", '"', "�", "ʿ", "·", "჻", "~", "՞",
                   "؟", "،", "।", "॥", "«", "»", "„", "“", "”", "「", "」", "‘", "’", "《", "》", "(", ")", "[", "]",
                   "{", "}", "=", "`", "_", "+", "<", ">", "…", "–", "°", "´", "ʾ", "‹", "›", "©", "®", "—", "→", "。",
                   "、", "﹂", "﹁", "‧", "～", "﹏", "，", "｛", "｝", "（", "）", "［", "］", "【", "】", "‥", "〽",
                   "『", "』", "〝", "〟", "⟨", "⟩", "〜", "：", "！", "？", "♪", "؛", "/", "\\", "º", "−", "^", "ʻ", "ˆ"]  


    chars_to_remove_regex = f"[{re.escape(''.join(chars_to_ignore_regex))}]"
    
    
    
    # remove punctuation
    text = re.sub(chars_to_remove_regex, '', text)
    
    text = text.lower()
    
    # Let's also make sure we split on all kinds of newlines, spaces, etc...
    #text = " ".join(text.split())
    
    return text

In [55]:
# map function to decode audio
def map_to_pred(batch):
    prediction = asr(
        batch["audio"]["array"]
    )

    batch["prediction"] = prediction["text"]
    batch["target"] = normalize_text(batch["sentence"])
    return batch

In [56]:
model_id = "RASMUS/wav2vec2-xlsr-fi-lm-1B"

asr = pipeline("automatic-speech-recognition", model=model_id, device=0)
# run inference on all examples
result = common_voice_dataset.map(map_to_pred, remove_columns=common_voice_dataset.column_names)

  0%|          | 0/1599 [00:00<?, ?ex/s]

/opt/conda/lib/python3.8/site-packages/transformers/pipelines/base.py:976: UserWarning: You seem to be using the pipelines sequentially on GPU. In order to maximize efficiency please use a dataset
  warnings.warn(


In [57]:
print("WER: {:2f}".format(100 * wer_metric.compute(predictions=result["prediction"], references=result["target"])))

WER: 27.110258
